# Group Assignment 3: Cleaned Midterm Notebook (2/2) #

## Carolyn Chu and Leslie Velasquez ##

## Section 4: Creating a Folium map of Los Angeles Parks ##
Next, we will import our parks data again to create an interactive map of parks in Los Angeles. We also create markers with the names and size of the park.

### 4a. Import Parks Data and Libraries ##

In [1]:
# import libraries
import urllib.request, json 
import pandas as pd   # for data analysis
import geopandas as gpd   # for analyzing spatial data
import contextily as ctx   # for base maps
import matplotlib.pyplot as plt   # for plotting data
import plotly.express as px   # for interactive plots
import folium   # for interactive maps
import osmnx as ox # to download osm data

/opt/conda/lib/python3.9/site-packages/geopandas/_compat.py:106: UserWarning: The Shapely GEOS version (3.9.1-CAPI-1.14.2) is incompatible with the GEOS version PyGEOS was compiled with (3.10.1-CAPI-1.16.0). Conversions between both will be slow.
  warnings.warn(


In [2]:
# import parks and recreate geojson file
parks = gpd.read_file('Recreation and Parks Information.geojson')

### 4b. Creating a Folium Map with Markers! ###

In [3]:
# first, we create a simple folium map without any data, centered on Los Angeles.
m = folium.Map(location=[34.05, -118.24], zoom_start=11, tiles='CartoDB positron')
m

In [4]:
# now we can overlay the polygons from the parks geojson file over the folium map. We make sure the popup corresponds to the park name

for _, r in parks.iterrows():
    sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'green'})
    folium.Popup(r['name_alpha']).add_to(geo_j)
    geo_j.add_to(m)
m

In [5]:
# to create markers centered on each park, we will need to determine the centroid of each park.
# to determine the centroids, we need to project the data into a different coordinate system that can work with geometries, NAD83. 

parks = parks.to_crs(epsg=2263)

parks['centroid'] = parks.centroid

In [6]:
# now we will need to project back to our lat/long projection to use folium.
# we also create a new column with the centroid of each park.

parks = parks.to_crs(epsg=4326)

parks['centroid'] = parks['centroid'].to_crs(epsg=4326)

In [7]:
# check to make sure changes were made.
parks.head()

name     shape_area objectid park_id  \
0  Robert F Kennedy Inspiration Memorial Park  6501.37488025        1    1056   
1                         Sycamore Grove Park  691462.199493        2     736   
2                      San Pedro Welcome Park  17402.1579777        3     328   
3                  Country Club Heritage Park  3647.84860118        4    1045   
4                     Watts Cultural Crescent  128793.355722        5    1046   

                          name_alpha     shape_leng       area_acres  \
0  ROBERT F KENNEDY PARK (LAUSD) JUA   641.47054538   0.149251627315   
1                SYCAMORE GROVE PARK   6227.3991903    15.8738513625   
2             SAN PEDRO WELCOME PARK  560.372862441   0.399500174163   
3   COUNTRY CLUB PARK HERITAGE PLAZA  287.523337381  0.0837434158085   
4            WATTS CULTURAL CRESCENT  2852.11033344    2.95670043382   

  issubpark region                           address  \
0         N      M    3400 W Wilshire Blvd, LA 90010   
1         N      M      4702 N Figueroa St, LA 90042   
2         N      P  451 N Gaffey St, San Pedro 90731   
3         N      M        1015 S Wilton Pl, LA 90018   
4         N      P   1780 E Santa Ana Blvd, LA 90002   

                                          name_publi park_class cd_real  \
0  Kennedy (Robert F) Inspiration Memorial Park (...          N      10   
1                                Sycamore Grove Park          C      01   
2                              Formerly Welcome Park          N      15   
3                              AKA Wilton Place Park          N      10   
4                  AKA Watts Towers Cultural Cresent          N      15   

                                            geometry  \
0  MULTIPOLYGON (((-118.29796 34.06162, -118.2969...   
1  MULTIPOLYGON (((-118.20110 34.10134, -118.2011...   
2  MULTIPOLYGON (((-118.29286 33.74600, -118.2928...   
3  MULTIPOLYGON (((-118.31504 34.05232, -118.3149...   
4  MULTIPOLYGON (((-118.24221 33.93945, -118.2422...   

                      centroid  
0  POINT (-118.29749 34.06159)  
1  POINT (-118.20301 34.10007)  
2  POINT (-118.29264 33.74621)  
3  POINT (-118.31481 34.05236)  
4  POINT (-118.24096 33.93896)

In [8]:
# Now we can finally plot our folium map, with the markers in the center of each park.
# We manipulate the code to make it so that when you scroll over a park, the name appears.
# We also make it so that when you click on a park, its area in acres appears.

for _, r in parks.iterrows():
    lat = r['centroid'].y
    lon = r['centroid'].x
    folium.Marker(location=[lat, lon],popup=r.area_acres, tooltip=r.name_alpha).add_to(m)
m

Like our static map comparing parks with the highest and lowest income census trats, this folium map shows a large number of parks throughout the city of Los Angeles. This appears contrary to prevailing research from community groups like the Los Angeles Neighborhood Land Trust and even the Department of Parks and Recreation’s Needs Assessment which found that more than half of Los Angeles County is considered “park poor,” with 82% of these areas located in communities of color.

Again, to us this suggests that parks equity is not merely a pure question of access, or “does a park exist in this area or not?” but rather proportion, or “what is the ratio of park space to population?” and quality “what funding and amenities does this park have?”

We will further explore these questions going forward in our project.